In [23]:
import numpy as np
import pandas as pd
from datetime import datetime, timedelta
import sys

In [24]:
excel_file = pd.read_excel("/Users/soniyaagarwal/Downloads/BITKUB ANALYSIS/>0.1/Book3.xlsx",sheet_name=None)
dataset_combined = pd.concat(excel_file.values())

In [25]:
df=pd.DataFrame(dataset_combined)

In [26]:
for col in df.columns:
    print(col)

["__v"
_id
bWAP
bltp
buyPrice
coin
create_at
eWAP
fp
margin
profit
profit_per
qty
recal
sellPrice
time
time_diff
type]
Unnamed: 2
Unnamed: 7
Unnamed: 9
Unnamed: 13
Unnamed: 16


In [27]:
df = df[df["profit_per"] >= 0.1]

In [28]:
df["time"] = df["time"].apply(lambda x: x[:24])
df["time"] = pd.to_datetime(df["time"], format="%d-%m-%Y, %H : %M : %S")
df.sort_values(by=["time"], ascending=True, inplace = True) # Sorting the Data frame in ascending order 
df['new_date'] = [d.date() for d in df["time"]]
df['new_time'] = [d.time() for d in df["time"]]
df['new_time'] = pd.to_datetime(df['new_time'] , format='%H:%M:%S')
df['hours'] = df['new_time'].dt.hour
df['minutes'] = df['new_time'].dt.minute
df['seconds'] = df['hours'] * 3600 + df['minutes'] * 60 + df['new_time'].dt.second # convert entire time to second
df = df.reset_index(drop = True)  # resetting the indexes

In [29]:
df['seconds_diff'] = df['seconds'].diff(periods = 1).abs()# find the second difference in absolute value terms
df.loc[0,['seconds_diff']] = [0] # updating first row of column 'seconds_diff' with 0

In [30]:
df['qty_match'] = df['qty'].diff().eq(0) # previous row item of qty are equal with next row item

In [31]:
# Cluster formation
global_count = 1

def myfunc(row):
    global global_count
    if row['seconds_diff'] >= 30 and row['qty_match'] is False:
        global_count += 1
    return global_count

# apply a function to each row to examine 'sweconds_diff' and 'qty_match' and generate value for 'cluster'
df['cluster'] = df.apply(lambda row: myfunc(row), axis=1)            

In [32]:
df2 = df.pivot_table(index=['cluster' , 'coin'], columns= None, values='qty' , aggfunc='max')
df2

qty
cluster coin                    
1       1INCHUSDT    6469.641677
        AAVEUSDT      695.658871
        ADAUSDT    139219.538819
        ALPHAUSDT  223975.826797
        APEUSDT     17983.278355
...                          ...
1609    YFIUSDT         2.055030
1610    GALAUSDT   310548.127388
        YFIUSDT         1.598320
1611    DOGEUSDT     9009.311784
1612    GALAUSDT   135075.337761

[2742 rows x 1 columns]

In [33]:
#df.to_excel("/Users/soniyaagarwal/Downloads/BITKUB ANALYSIS/>0.1/Book3_new.xlsx")

In [34]:
#df2.to_excel("/Users/soniyaagarwal/Downloads/BITKUB ANALYSIS/>0.1/Book3_new.xlsx")